<a href="https://colab.research.google.com/github/justdaksh/ImageToStory/blob/main/Image_to_Story_to_Audio.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import tensorflow as tf
tf.test.gpu_device_name()

'/device:GPU:0'

In [2]:
# imports
!pip install transformers scipy Ipython optimum accelerate

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 399.9/399.9 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 261.4/261.4 kB 26.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 35.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.0/46.0 kB 5.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 521.2/521.2 kB 34.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 54.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.8/86.8 kB 9.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 18.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 18.9 MB/s eta 0:00:00


In [3]:
from transformers import pipeline, BarkProcessor, BarkModel
import os,requests
from scipy.io.wavfile import write
from google.colab import userdata
from IPython.display import Audio, display
from optimum.bettertransformer import BetterTransformer
import nltk  # we'll use this to split into sentences
nltk.download('punkt')
import numpy as np
HUGGINGFACE_API_TOKEN = userdata.get('HUGGINGFACE_API_TOKEN')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


In [9]:
# image to text
def imageToText():
    captioner = pipeline("image-to-text",model="Salesforce/blip-image-captioning-base")
    img_url = "/content/ChohanTemplate.jpg"
    result = captioner(img_url)
    print(result[0]["generated_text"])
    return result[0]["generated_text"]

# text to story
def textToStory(scenario):
    API_URL = "https://api-inference.huggingface.co/models/tiiuae/falcon-7b-instruct"
    headers = {"Authorization": f"Bearer {HUGGINGFACE_API_TOKEN}"}
    template = f"You are a story teller.You can generate a story base on a simple narrative. Story should be not more than 30 words and Don't make up something that is not in the picture. Keep the story believeable; CONTEXT: {scenario} STORY:"

    def query(payload):
        response = requests.post(API_URL, headers=headers, json=payload)
        return response.json()

    output = query({
        "inputs": template,
    })
    story = output[0]["generated_text"].split("STORY:", 1)[-1].strip()
    print(story)
    return story

# text to speech
def textToSpeech(prompt):
    processor = BarkProcessor.from_pretrained("suno/bark-small")
    model = BarkModel.from_pretrained("suno/bark-small")
    model = BetterTransformer.transform(model, keep_original_model=False)
    voice_preset = "v2/en_speaker_6"
    sample_rate = model.generation_config.sample_rate
    # Tokenizing
    GEN_TEMP = 0.6
    sentences = nltk.sent_tokenize(prompt)
    silence = np.zeros(int(0.25 * sample_rate))
    pieces = []
    for sentence in sentences:
        inputs = processor(sentence, voice_preset=voice_preset)
        audio_array = model.generate(**inputs,fine_temperature=GEN_TEMP,min_eos_p=0.05)
        audio_array = audio_array.cpu().numpy().squeeze()
        pieces += [audio_array, silence.copy()]

    write("MyStory.wav", rate=sample_rate, data=audio_array)
    display(Audio(np.concatenate(pieces), rate=sample_rate))


In [5]:
text = imageToText()

config.json:   0%|          | 0.00/4.56k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/990M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/506 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/711k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

preprocessor_config.json:   0%|          | 0.00/287 [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1273: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(


a man sitting on a couch holding a cell


In [6]:
story = textToStory(text)

The man sat on his comfortable couch, scrolling through his phone. He absentmindedly ate a sandwich, his mind elsewhere. Suddenly, his phone rang. With a start, he looked at the screen, his heart racing. It was an unfamiliar number. He hesitated before answering, his voice shaky. 'Hello?' he whispered. The voice on the other end, calm and collected, introduced itself as a mysterious voice from the past. The man's heart pounded as he listened to the voice recounting a tale of a long-lost treasure. The voice promised riches beyond his wildest dreams, and the man couldn't resist the temptation. Without hesitation, he agreed. The voice instructed him on the steps to take, and the man set out on an adventure he never could have imagined.


In [10]:
textToSpeech(story)

The BetterTransformer implementation does not support padding during training, as the fused kernels do not support attention masks. Beware that passing padded batched data during training may result in unexpected outputs. Please refer to https://huggingface.co/docs/optimum/bettertransformer/overview for more details.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
